In [134]:
import networkx as nx
import pandas as pd
import geopandas as gpd
import numpy as np
import momepy
from shapely.geometry import Point, MultiLineString, LineString
from shapely.ops import nearest_points

In [153]:
road = gpd.read_file('data/link_data.gpkg')

# 각 링크별 길이 계산 (단위: 미터)
road['road_length(km)'] = road.geometry.length/1000

#열 이름 변경
#road = road.rename(columns={
#    'link_id': 'road_id',
#    'sigungu_id': 'road_sigungu_id'
#})

#필요한 열만 추출 
#road = road[['road_id', 'road_name', 'road_rank','road_sigungu_id','oneway', 'geometry','road_length(km)']]

In [154]:
speeds = pd.read_csv('data/speed_data.csv')

# 열 이름 영어로 변경
speeds = speeds.rename(columns={
    '﻿level6 LINK ID': 'link_id', 
    '평균속도 (km/h)': 'link_avsp',
    '도로등급': 'link_lev',
})
speeds

In [156]:
# 도로등급별 평균속도 계산
road_rank_avg_speed = speeds.groupby('link_lev')['link_avsp'].mean().to_dict()

# link_avsp를 float 타입으로 변환 (null 값이 있는지 확인 전에 타입 변경)
speeds['link_avsp'] = speeds['link_avsp'].astype(float)

# Null 값 처리
def fill_avsp(row, avg_dict):
    if pd.isnull(row['link_avsp']):
        return avg_dict.get(row['link_lev'], np.nan)
    else:
        return row['link_avsp']

speeds['link_avsp'] = speeds.apply(lambda row: fill_avsp(row, road_rank_avg_speed), axis=1)

In [157]:
# 도로 등급에 따른 숫자 지정
link_lev_to_rank = {
    '연결로': 108,
    '시군도': 107,
    '지방도': 106,
    '국가지원지방도': 105,
    '특별광역시도': 104,
    '일반국도': 103,
    '도시고속국도': 102,
    '고속도로': 101,
}
speeds['link_rank'] = speeds['link_lev'].map(link_lev_to_rank)

In [158]:
# 'alink_id'의 앞자리부터 9자리만 사용하여 'modified_link_id' 생성
speeds['modified_link_id'] = speeds['link_id'].apply(lambda x: str(x)[:9])

# modified_link_id와 link_lev를 기준으로 그룹화 후 link_avsp의 평균 계산
speeds_final = speeds.groupby(['modified_link_id', 'link_lev', 'link_rank'])['link_avsp'].mean().reset_index()

In [ ]:
# speeds_final과 road를 link_data로 지정
road['link_id'] = road['link_id'].astype(str)
link_data = road.merge(speeds_final, how='left', left_on='link_id', right_on='modified_link_id')
link_data

In [160]:
# 'link_rank' 별로 그룹화 후 'link_avsp'의 평균을 계산
rank_ave_speed = link_data.groupby('road_rank')['link_avsp'].mean().to_dict()

# link_avsp의 NaN 값을 해당 road_rank의 평균값으로 기입
link_data['link_avsp'] = link_data.apply(
    lambda row: rank_ave_speed[row['road_rank']] if pd.isnull(row['link_avsp']) else row['link_avsp'],
    axis=1
)

In [161]:
#link_data에 시간을 hour와 min, 분:초 형식으로 시간 변환한 열 추가
link_data['time(m)'] = link_data['road_length(km)']/link_data['link_avsp']*60
link_data['oneway'] = link_data['oneway'].map({1: True, 0: False})

In [196]:
# 도로 네트워크에서 모든 노드(시작점과 끝점)를 추출하는 함수
def extract_nodes(geometry):
    if isinstance(geometry, MultiLineString):
        return [Point(line.coords[0]) for line in geometry.geoms] + \
               [Point(line.coords[-1]) for line in geometry.geoms]
    elif isinstance(geometry, LineString):
        return [Point(geometry.coords[0]), Point(geometry.coords[-1])]
    else:
        raise ValueError(f"Unhandled geometry type: {type(geometry)}")

# link_data로부터 노드를 추출하여 nodes_gdf 생성
all_nodes = []
for _, row in link_data.iterrows():
    all_nodes.extend(extract_nodes(row['geometry']))

nodes_gdf = gpd.GeoDataFrame(geometry=all_nodes)

In [232]:
# nodes_gdf로부터 그래프 생성
G = nx.DiGraph() # 방향이 있는 그래프 생성
for index, row in link_data.iterrows():
    geom = row['geometry']
    # LineString 객체 처리
    if isinstance(geom, LineString):
        start_point = geom.coords[0]  # 시작점
        end_point = geom.coords[-1]  # 끝점
        time = geom.length/1000 # 추출한 Line별로(MultiLineString이 아님) 길이를 재산정
        G.add_edge(start_point, end_point, weight=dist/row['link_avsp']*60)
        
        if row['oneway'] == False: # 양방통행의 경우 동일한 edge를 반대방향으로 하나 더 추가
            start_point = geom.coords[-1]  # 시작점
            end_point = geom.coords[0]  # 끝점
            time = geom.length/1000 # 추출한 Line별로(MultiLineString이 아님) 길이를 재산정
            G.add_edge(start_point, end_point, weight=dist/row['link_avsp']*60)
        
    # MultiLineString 객체 처리
    elif isinstance(geom, MultiLineString):
        for line in geom.geoms:
            start_point = line.coords[0]  # 시작점
            end_point = line.coords[-1]  # 끝점
            dist = line.length/1000 # 추출한 Line별로(MultiLineString이 아님) 길이를 재산정
            G.add_edge(start_point, end_point, weight=dist/row['link_avsp']*60)

            if row['oneway'] == False: # 양방통행의 경우 동일한 edge를 반대방향으로 하나 더 추가
                start_point = line.coords[-1]  # 시작점
                end_point = line.coords[0]  # 끝점
                time = line.length/1000 # 추출한 Line별로(MultiLineString이 아님) 길이를 재산정
                G.add_edge(start_point, end_point, weight=dist/row['link_avsp']*60)

In [233]:
for u, v, edge in G.edges(data=True):
    print(u, v, edge)

(954878.90183511, 1815326.47092112) (954881.14757197, 1815321.07823996) {'weight': 0.010566411502686515}
(954878.90183511, 1815326.47092112) (954742.16164941, 1815491.86097161) {'weight': 0.364548514404782}
(954881.14757197, 1815321.07823996) (954878.90183511, 1815326.47092112) {'weight': 0.010566411502686515}
(954881.14757197, 1815321.07823996) (954888.03325381, 1815294.27987327) {'weight': 0.06707599173434185}
(954888.03325381, 1815294.27987327) (954881.14757197, 1815321.07823996) {'weight': 0.06707599173434185}
(954888.03325381, 1815294.27987327) (954891.24301649, 1815283.67533345) {'weight': 0.028592668119175022}
(954348.54043468, 1813477.04268913) (954733.74045242, 1813137.93484406) {'weight': 1.0330412903624686}
(954348.54043468, 1813477.04268913) (954360.53940003, 1813482.44630839) {'weight': 0.025392569041576454}
(954348.54043468, 1813477.04268913) (954341.25596606, 1813502.43326652) {'weight': 0.050969842883126594}
(954733.74045242, 1813137.93484406) (954348.54043468, 1813477.

In [198]:
# 가장 가까운 노드를 찾는 함수
def find_nearest_node(point, nodes_gdf):
    nearest_geom = nearest_points(point, nodes_gdf.unary_union)[1]
    nearest_node = nodes_gdf[nodes_gdf.geometry == nearest_geom].geometry.iloc[0]
    return nearest_node

In [199]:
sup = pd.read_csv("data/selected_doctor.csv")
sup = sup.rename(columns={
    '요양기관명': 'sup_name', 
    '종별코드명': 'sup_cate', 
    '시군구코드명': 'sup_sigungu', 
    '진료과목코드명': 'sup_doc_code', 
    '과목별 전문의수': 'sup_doc', 
    '좌표(X)': 'sup_x', 
    '좌표(Y)': 'sup_y'})
# 필터링 (필요한 부분을 필터링) *수정
fil_sup = sup[(sup['sup_doc_code'] == "소아청소년과") & (sup['sup_doc'] >= 1) & (sup['sup_sigungu'].str.startswith('세종시'))]

#각 공급지 마다 번호 부여하기 위해 y좌표 기준 오름차순 정리
fil_sup = fil_sup.sort_values(by='sup_y')

# 오름차순 정리 후 순서대로 번호 부여
fil_sup = fil_sup.reset_index(drop=True)
fil_sup['sup_num'] = fil_sup.index + 1

# x,y를 공간 데이터로 변환
sup_sf = gpd.GeoDataFrame(
    fil_sup, 
    geometry=gpd.points_from_xy(fil_sup['sup_x'], fil_sup['sup_y']),
    crs="EPSG:4326"  # 원본 좌표계 설정
).to_crs(5179)

# 불필요한 열 삭제 *수정
sup_sf = sup_sf[['sup_num', 'sup_name', 'geometry']]

In [248]:
sup_sf.iloc[0:1]['geometry'].to_crs(4326)

0    POINT (127.28971 36.47725)
Name: geometry, dtype: geometry

In [226]:
# 중심점 불러오기
centroid_df = gpd.read_file("data/1000centroid_df.gpkg")
centroid_df.iloc[0:124]['geometry'].to_crs(4326)

0      POINT (127.34920 36.52611)
1      POINT (127.23754 36.51690)
2      POINT (127.29345 36.48997)
3      POINT (127.22640 36.50786)
4      POINT (127.24894 36.44481)
                  ...            
119    POINT (127.22662 36.44476)
120    POINT (127.25987 36.51695)
121    POINT (127.30464 36.48097)
122    POINT (127.23708 36.65213)
123    POINT (127.27128 36.43584)
Name: geometry, Length: 124, dtype: geometry

In [236]:
# 결과를 저장할 리스트
results = []

# 각 중심점과 병원 간 최단 경로 이동 시간 계산
for idx_c, centroid in centroid_df.iterrows():
    source_name = centroid['gid']
    source_point = centroid['geometry']
    source_node = find_nearest_node(source_point, nodes_gdf)
    
    source_to_node_distance = source_point.distance(source_node)
    source_to_node_time = (source_to_node_distance/1000) / (30 / 60)  # km/m로 변환 후 시간 계산

    for idx_h, sup in sup_sf.iloc[0:1].iterrows():
        target_name = sup['sup_name']
        target_point = sup['geometry']
        target_node = find_nearest_node(target_point, nodes_gdf)
        
        target_to_node_distance = target_point.distance(target_node)
        target_to_node_time = (target_to_node_distance/1000) / (30 / 60)  # km/m로 변환 후 시간 계산

        try:
            # 네트워크를 통한 최단 경로 이동 시간 계산
            network_path_time = nx.shortest_path_length(G, source=source_node.coords[0], target=target_node.coords[0], weight='weight')
            
            # 최종 비용 계산: 네트워크 최단 경로 시간 + 직선 거리 이동 시간
            total_cost = network_path_time + source_to_node_time + target_to_node_time  # 분 단위로 변환

            results.append({'source': idx_c, 'source_name': source_name, 
                            'target': idx_h, 'target_name': target_name,
                            'source_cost': source_to_node_time, 'target_cost': target_to_node_time, 
                            'total_cost': total_cost})
        except nx.NetworkXNoPath:
            continue

# 결과를 DataFrame으로 변환
df_results = pd.DataFrame(results)


In [237]:
df_results

source source_name  target target_name  source_cost  target_cost  \
0         0      다바8636       0  고운소아청소년과의원     0.965505     0.090803   
1         1      다바7635       0  고운소아청소년과의원     0.125943     0.090803   
2         2      다바8132       0  고운소아청소년과의원     0.782417     0.090803   
3         3      다바7534       0  고운소아청소년과의원     0.708439     0.090803   
4         4      다바7727       0  고운소아청소년과의원     0.366772     0.090803   
..      ...         ...     ...         ...          ...          ...   
119     119      다바7527       0  고운소아청소년과의원     0.967579     0.090803   
120     120      다바7835       0  고운소아청소년과의원     0.134066     0.090803   
121     121      다바8231       0  고운소아청소년과의원     0.159766     0.090803   
122     122      다바7650       0  고운소아청소년과의원     2.181443     0.090803   
123     123      다바7926       0  고운소아청소년과의원     0.536190     0.090803   

     total_cost  
0     16.260203  
1     13.246166  
2      4.429394  
3     14.964959  
4     12.627927  
..          ...  
119   11.448433  
120   12.574231  
121    4.353742  
122   37.173133  
123   11.553355  

[124 rows x 7 columns]

In [243]:
# MultiLineString을 LineString으로 변환
single_link_data = link_data.explode(ignore_index=True)


OutEdgeDataView([((954878.90183511, 1815326.47092112), (954881.14757197, 1815321.07823996), {'weight': 0.010566411502686515}), ((954878.90183511, 1815326.47092112), (954742.16164941, 1815491.86097161), {'weight': 0.364548514404782}), ((954881.14757197, 1815321.07823996), (954878.90183511, 1815326.47092112), {'weight': 0.010566411502686515}), ((954881.14757197, 1815321.07823996), (954888.03325381, 1815294.27987327), {'weight': 0.06707599173434185}), ((954888.03325381, 1815294.27987327), (954881.14757197, 1815321.07823996), {'weight': 0.06707599173434185}), ((954888.03325381, 1815294.27987327), (954891.24301649, 1815283.67533345), {'weight': 0.028592668119175022}), ((954348.54043468, 1813477.04268913), (954733.74045242, 1813137.93484406), {'weight': 1.0330412903624686}), ((954348.54043468, 1813477.04268913), (954360.53940003, 1813482.44630839), {'weight': 0.025392569041576454}), ((954348.54043468, 1813477.04268913), (954341.25596606, 1813502.43326652), {'weight': 0.050969842883126594}), 

In [109]:
G = momepy.gdf_to_nx(single_link_data, approach = 'primal', directed = True, oneway_column= 'oneway')